In [21]:
import numpy as np
import pandas as pd
import scipy.sparse as ss
import os, io, base64

In [22]:
# SCIPY SPARSE COO DOES NOT CONTAIN HEADER INFORMATION
# CREATE A SEPARATE ENCODING OF HEADER BY PUTTING HEADER AS HEADER OF A PANDAS DATAFRAME, AND ENCODE THAT
s
# IMPORTANT NOTES FOR EMBEDDING A SCIPY SPARSE COO
# 1) WHEN CREATING THE COO, MUST SPECIFY A NUMERICAL dtype (IE np.int8, np.float64) --- CANNOT SAY object
# 2) WHEN CREATING THE NPZ FILE, compressed MUST BE True

In [23]:
# ENCODE

def scipy_sparse_coo_encoder(HEADER_AS_NP_RAVEL, DATA_AS_NP_ARRAY):
    
    if os.name=='nt': desktop_path = r'c:\users\bill\desktop'
    elif os.name=='posix': desktop_path = r'/home/bear/Desktop'

    
    # ENCODE HEADER ####################################################################################
    hdr_filename = 'base64_coo_header_dump.txt'
    
    hdr_path_and_file_name = os.path.join(desktop_path, hdr_filename)
    
    with open(hdr_path_and_file_name, 'w') as f:
        f.write(base64.b64encode(pd.DataFrame(columns=HEADER).to_csv(index=False).encode('utf-8')).decode('utf-8'))
    # END ENCODE HEADER #################################################################################
    
    # ENCODE DATA AS COO ################################################################################

    coo_filename = 'base64_coo_data_dump.txt'
    
    coo_path_and_file_name = os.path.join(desktop_path, coo_filename)
    
    # ss.save_npz OUTPUT CAN ONLY BE WRITTEN TO A FILE-LIKE OBJECT, A PATH OR FILE-LIKE OBJECT MUST BE PASSED TO IT. 
    # UNLIKE PANDAS .to_csv(), WHERE IF A PATH IS PASSED IT WILL WRITE TO IT, BUT IF NO PATH IS GIVEN IT RETURNS THE 
    # BINARY FILE TO THE PYTHON SESSION
    # THEREFORE CREATE A FILE-LIKE RECEPTACLE FOR THE BINARY npz FILE
    dummy_io = io.BytesIO()

    
    # TRANSFORM NUMPY NDARRAY TO scipy.sparse.coo_array OR coo_matrix
    # scipy.sparse.coo_matrix(arg1, shape=None, dtype=None, copy=False)
    
    # DATA_COO = ss.coo_array(DATA_AS_NP_ARRAY, dtype=np.float64)   # <===== dtype MUST BE SPECIFIED AND CANNOT BE "object" !!!
    # --- OR ---
    COO_MATRIX = ss.coo_matrix(DATA_AS_NP_ARRAY, dtype=np.float64)   # <==== dtype MUST BE NUMERICAL dtype, NOT object

    # dtype REQUIREMENT FORCES ALL coo_arrays TO BE NUMBERS, THEREFORE CANNOT CONTAIN strs.
    # str COLUMNS WOULD HAVE TO BE SAVED SEPARATELY OR ANOTHER WAY.
    
    ss.save_npz(dummy_io, COO_MATRIX, compressed=True)  # <==== compressed MUST BE True

    del COO_MATRIX

    # ENCODE DATA AS COO ################################################################################
    with open(coo_path_and_file_name, 'w') as f:
        f.write(base64.b64encode(dummy_io.getvalue()).decode('utf-8'))


    del dummy_io

In [24]:
# DECODE

# header_embed = ''
# data_embed = ''

# HEADER
# HEADER_DF = pd.read_csv(io.BytesIO(base64.b64decode(header_embed)))

# DATA
# DATA_NP = ss.load_npz(io.BytesIO(base64.b64decode(data_embed))).toarray()

# COMBINE
# DATA = pd.DataFrame(data=DATA_NP, columns=HEADER_DF.columns, dtype=np.float64)

In [25]:
# os.remove(hdr_path_and_file_name)
# os.remove(coo_path_and_file_name)

#### DEMO ****************************************************************************************************

In [26]:
# CREATE DUMMY DATA AND HEADER
DATA = np.random.randint(0,2,(10_000,1_000),dtype=np.uint8)

HEADER = np.fromiter(map(lambda x: str(x).rjust(4, '0'), np.linspace(1, 1000, num=1000, dtype=np.uint16).astype('<U4')), dtype='<U4')

In [27]:
scipy_sparse_coo_encoder(HEADER, DATA)

In [28]:
header_embed = 'MDAwMSwwMDAyLDAwMDMsMDAwNCwwMDA1LDAwMDYsMDAwNywwMDA4LDAwMDksMDAxMCwwMDExLDAwMTIsMDAxMywwMDE0LDAwMTUsMDAxNiwwMDE3LDAwMTgsMDAxOSwwMDIwLDAwMjEsMDAyMiwwMDIzLDAwMjQsMDAyNSwwMDI2LDAwMjcsMDAyOCwwMDI5LDAwMzAsMDAzMSwwMDMyLDAwMzMsMDAzNCwwMDM1LDAwMzYsMDAzNywwMDM4LDAwMzksMDA0MCwwMDQxLDAwNDIsMDA0MywwMDQ0LDAwNDUsMDA0NiwwMDQ3LDAwNDgsMDA0OSwwMDUwLDAwNTEsMDA1MiwwMDUzLDAwNTQsMDA1NSwwMDU2LDAwNTcsMDA1OCwwMDU5LDAwNjAsMDA2MSwwMDYyLDAwNjMsMDA2NCwwMDY1LDAwNjYsMDA2NywwMDY4LDAwNjksMDA3MCwwMDcxLDAwNzIsMDA3MywwMDc0LDAwNzUsMDA3NiwwMDc3LDAwNzgsMDA3OSwwMDgwLDAwODEsMDA4MiwwMDgzLDAwODQsMDA4NSwwMDg2LDAwODcsMDA4OCwwMDg5LDAwOTAsMDA5MSwwMDkyLDAwOTMsMDA5NCwwMDk1LDAwOTYsMDA5NywwMDk4LDAwOTksMDEwMCwwMTAxLDAxMDIsMDEwMywwMTA0LDAxMDUsMDEwNiwwMTA3LDAxMDgsMDEwOSwwMTEwLDAxMTEsMDExMiwwMTEzLDAxMTQsMDExNSwwMTE2LDAxMTcsMDExOCwwMTE5LDAxMjAsMDEyMSwwMTIyLDAxMjMsMDEyNCwwMTI1LDAxMjYsMDEyNywwMTI4LDAxMjksMDEzMCwwMTMxLDAxMzIsMDEzMywwMTM0LDAxMzUsMDEzNiwwMTM3LDAxMzgsMDEzOSwwMTQwLDAxNDEsMDE0MiwwMTQzLDAxNDQsMDE0NSwwMTQ2LDAxNDcsMDE0OCwwMTQ5LDAxNTAsMDE1MSwwMTUyLDAxNTMsMDE1NCwwMTU1LDAxNTYsMDE1NywwMTU4LDAxNTksMDE2MCwwMTYxLDAxNjIsMDE2MywwMTY0LDAxNjUsMDE2NiwwMTY3LDAxNjgsMDE2OSwwMTcwLDAxNzEsMDE3MiwwMTczLDAxNzQsMDE3NSwwMTc2LDAxNzcsMDE3OCwwMTc5LDAxODAsMDE4MSwwMTgyLDAxODMsMDE4NCwwMTg1LDAxODYsMDE4NywwMTg4LDAxODksMDE5MCwwMTkxLDAxOTIsMDE5MywwMTk0LDAxOTUsMDE5NiwwMTk3LDAxOTgsMDE5OSwwMjAwLDAyMDEsMDIwMiwwMjAzLDAyMDQsMDIwNSwwMjA2LDAyMDcsMDIwOCwwMjA5LDAyMTAsMDIxMSwwMjEyLDAyMTMsMDIxNCwwMjE1LDAyMTYsMDIxNywwMjE4LDAyMTksMDIyMCwwMjIxLDAyMjIsMDIyMywwMjI0LDAyMjUsMDIyNiwwMjI3LDAyMjgsMDIyOSwwMjMwLDAyMzEsMDIzMiwwMjMzLDAyMzQsMDIzNSwwMjM2LDAyMzcsMDIzOCwwMjM5LDAyNDAsMDI0MSwwMjQyLDAyNDMsMDI0NCwwMjQ1LDAyNDYsMDI0NywwMjQ4LDAyNDksMDI1MCwwMjUxLDAyNTIsMDI1MywwMjU0LDAyNTUsMDI1NiwwMjU3LDAyNTgsMDI1OSwwMjYwLDAyNjEsMDI2MiwwMjYzLDAyNjQsMDI2NSwwMjY2LDAyNjcsMDI2OCwwMjY5LDAyNzAsMDI3MSwwMjcyLDAyNzMsMDI3NCwwMjc1LDAyNzYsMDI3NywwMjc4LDAyNzksMDI4MCwwMjgxLDAyODIsMDI4MywwMjg0LDAyODUsMDI4NiwwMjg3LDAyODgsMDI4OSwwMjkwLDAyOTEsMDI5MiwwMjkzLDAyOTQsMDI5NSwwMjk2LDAyOTcsMDI5OCwwMjk5LDAzMDAsMDMwMSwwMzAyLDAzMDMsMDMwNCwwMzA1LDAzMDYsMDMwNywwMzA4LDAzMDksMDMxMCwwMzExLDAzMTIsMDMxMywwMzE0LDAzMTUsMDMxNiwwMzE3LDAzMTgsMDMxOSwwMzIwLDAzMjEsMDMyMiwwMzIzLDAzMjQsMDMyNSwwMzI2LDAzMjcsMDMyOCwwMzI5LDAzMzAsMDMzMSwwMzMyLDAzMzMsMDMzNCwwMzM1LDAzMzYsMDMzNywwMzM4LDAzMzksMDM0MCwwMzQxLDAzNDIsMDM0MywwMzQ0LDAzNDUsMDM0NiwwMzQ3LDAzNDgsMDM0OSwwMzUwLDAzNTEsMDM1MiwwMzUzLDAzNTQsMDM1NSwwMzU2LDAzNTcsMDM1OCwwMzU5LDAzNjAsMDM2MSwwMzYyLDAzNjMsMDM2NCwwMzY1LDAzNjYsMDM2NywwMzY4LDAzNjksMDM3MCwwMzcxLDAzNzIsMDM3MywwMzc0LDAzNzUsMDM3NiwwMzc3LDAzNzgsMDM3OSwwMzgwLDAzODEsMDM4MiwwMzgzLDAzODQsMDM4NSwwMzg2LDAzODcsMDM4OCwwMzg5LDAzOTAsMDM5MSwwMzkyLDAzOTMsMDM5NCwwMzk1LDAzOTYsMDM5NywwMzk4LDAzOTksMDQwMCwwNDAxLDA0MDIsMDQwMywwNDA0LDA0MDUsMDQwNiwwNDA3LDA0MDgsMDQwOSwwNDEwLDA0MTEsMDQxMiwwNDEzLDA0MTQsMDQxNSwwNDE2LDA0MTcsMDQxOCwwNDE5LDA0MjAsMDQyMSwwNDIyLDA0MjMsMDQyNCwwNDI1LDA0MjYsMDQyNywwNDI4LDA0MjksMDQzMCwwNDMxLDA0MzIsMDQzMywwNDM0LDA0MzUsMDQzNiwwNDM3LDA0MzgsMDQzOSwwNDQwLDA0NDEsMDQ0MiwwNDQzLDA0NDQsMDQ0NSwwNDQ2LDA0NDcsMDQ0OCwwNDQ5LDA0NTAsMDQ1MSwwNDUyLDA0NTMsMDQ1NCwwNDU1LDA0NTYsMDQ1NywwNDU4LDA0NTksMDQ2MCwwNDYxLDA0NjIsMDQ2MywwNDY0LDA0NjUsMDQ2NiwwNDY3LDA0NjgsMDQ2OSwwNDcwLDA0NzEsMDQ3MiwwNDczLDA0NzQsMDQ3NSwwNDc2LDA0NzcsMDQ3OCwwNDc5LDA0ODAsMDQ4MSwwNDgyLDA0ODMsMDQ4NCwwNDg1LDA0ODYsMDQ4NywwNDg4LDA0ODksMDQ5MCwwNDkxLDA0OTIsMDQ5MywwNDk0LDA0OTUsMDQ5NiwwNDk3LDA0OTgsMDQ5OSwwNTAwLDA1MDEsMDUwMiwwNTAzLDA1MDQsMDUwNSwwNTA2LDA1MDcsMDUwOCwwNTA5LDA1MTAsMDUxMSwwNTEyLDA1MTMsMDUxNCwwNTE1LDA1MTYsMDUxNywwNTE4LDA1MTksMDUyMCwwNTIxLDA1MjIsMDUyMywwNTI0LDA1MjUsMDUyNiwwNTI3LDA1MjgsMDUyOSwwNTMwLDA1MzEsMDUzMiwwNTMzLDA1MzQsMDUzNSwwNTM2LDA1MzcsMDUzOCwwNTM5LDA1NDAsMDU0MSwwNTQyLDA1NDMsMDU0NCwwNTQ1LDA1NDYsMDU0NywwNTQ4LDA1NDksMDU1MCwwNTUxLDA1NTIsMDU1MywwNTU0LDA1NTUsMDU1NiwwNTU3LDA1NTgsMDU1OSwwNTYwLDA1NjEsMDU2MiwwNTYzLDA1NjQsMDU2NSwwNTY2LDA1NjcsMDU2OCwwNTY5LDA1NzAsMDU3MSwwNTcyLDA1NzMsMDU3NCwwNTc1LDA1NzYsMDU3NywwNTc4LDA1NzksMDU4MCwwNTgxLDA1ODIsMDU4MywwNTg0LDA1ODUsMDU4NiwwNTg3LDA1ODgsMDU4OSwwNTkwLDA1OTEsMDU5MiwwNTkzLDA1OTQsMDU5NSwwNTk2LDA1OTcsMDU5OCwwNTk5LDA2MDAsMDYwMSwwNjAyLDA2MDMsMDYwNCwwNjA1LDA2MDYsMDYwNywwNjA4LDA2MDksMDYxMCwwNjExLDA2MTIsMDYxMywwNjE0LDA2MTUsMDYxNiwwNjE3LDA2MTgsMDYxOSwwNjIwLDA2MjEsMDYyMiwwNjIzLDA2MjQsMDYyNSwwNjI2LDA2MjcsMDYyOCwwNjI5LDA2MzAsMDYzMSwwNjMyLDA2MzMsMDYzNCwwNjM1LDA2MzYsMDYzNywwNjM4LDA2MzksMDY0MCwwNjQxLDA2NDIsMDY0MywwNjQ0LDA2NDUsMDY0NiwwNjQ3LDA2NDgsMDY0OSwwNjUwLDA2NTEsMDY1MiwwNjUzLDA2NTQsMDY1NSwwNjU2LDA2NTcsMDY1OCwwNjU5LDA2NjAsMDY2MSwwNjYyLDA2NjMsMDY2NCwwNjY1LDA2NjYsMDY2NywwNjY4LDA2NjksMDY3MCwwNjcxLDA2NzIsMDY3MywwNjc0LDA2NzUsMDY3NiwwNjc3LDA2NzgsMDY3OSwwNjgwLDA2ODEsMDY4MiwwNjgzLDA2ODQsMDY4NSwwNjg2LDA2ODcsMDY4OCwwNjg5LDA2OTAsMDY5MSwwNjkyLDA2OTMsMDY5NCwwNjk1LDA2OTYsMDY5NywwNjk4LDA2OTksMDcwMCwwNzAxLDA3MDIsMDcwMywwNzA0LDA3MDUsMDcwNiwwNzA3LDA3MDgsMDcwOSwwNzEwLDA3MTEsMDcxMiwwNzEzLDA3MTQsMDcxNSwwNzE2LDA3MTcsMDcxOCwwNzE5LDA3MjAsMDcyMSwwNzIyLDA3MjMsMDcyNCwwNzI1LDA3MjYsMDcyNywwNzI4LDA3MjksMDczMCwwNzMxLDA3MzIsMDczMywwNzM0LDA3MzUsMDczNiwwNzM3LDA3MzgsMDczOSwwNzQwLDA3NDEsMDc0MiwwNzQzLDA3NDQsMDc0NSwwNzQ2LDA3NDcsMDc0OCwwNzQ5LDA3NTAsMDc1MSwwNzUyLDA3NTMsMDc1NCwwNzU1LDA3NTYsMDc1NywwNzU4LDA3NTksMDc2MCwwNzYxLDA3NjIsMDc2MywwNzY0LDA3NjUsMDc2NiwwNzY3LDA3NjgsMDc2OSwwNzcwLDA3NzEsMDc3MiwwNzczLDA3NzQsMDc3NSwwNzc2LDA3NzcsMDc3OCwwNzc5LDA3ODAsMDc4MSwwNzgyLDA3ODMsMDc4NCwwNzg1LDA3ODYsMDc4NywwNzg4LDA3ODksMDc5MCwwNzkxLDA3OTIsMDc5MywwNzk0LDA3OTUsMDc5NiwwNzk3LDA3OTgsMDc5OSwwODAwLDA4MDEsMDgwMiwwODAzLDA4MDQsMDgwNSwwODA2LDA4MDcsMDgwOCwwODA5LDA4MTAsMDgxMSwwODEyLDA4MTMsMDgxNCwwODE1LDA4MTYsMDgxNywwODE4LDA4MTksMDgyMCwwODIxLDA4MjIsMDgyMywwODI0LDA4MjUsMDgyNiwwODI3LDA4MjgsMDgyOSwwODMwLDA4MzEsMDgzMiwwODMzLDA4MzQsMDgzNSwwODM2LDA4MzcsMDgzOCwwODM5LDA4NDAsMDg0MSwwODQyLDA4NDMsMDg0NCwwODQ1LDA4NDYsMDg0NywwODQ4LDA4NDksMDg1MCwwODUxLDA4NTIsMDg1MywwODU0LDA4NTUsMDg1NiwwODU3LDA4NTgsMDg1OSwwODYwLDA4NjEsMDg2MiwwODYzLDA4NjQsMDg2NSwwODY2LDA4NjcsMDg2OCwwODY5LDA4NzAsMDg3MSwwODcyLDA4NzMsMDg3NCwwODc1LDA4NzYsMDg3NywwODc4LDA4NzksMDg4MCwwODgxLDA4ODIsMDg4MywwODg0LDA4ODUsMDg4NiwwODg3LDA4ODgsMDg4OSwwODkwLDA4OTEsMDg5MiwwODkzLDA4OTQsMDg5NSwwODk2LDA4OTcsMDg5OCwwODk5LDA5MDAsMDkwMSwwOTAyLDA5MDMsMDkwNCwwOTA1LDA5MDYsMDkwNywwOTA4LDA5MDksMDkxMCwwOTExLDA5MTIsMDkxMywwOTE0LDA5MTUsMDkxNiwwOTE3LDA5MTgsMDkxOSwwOTIwLDA5MjEsMDkyMiwwOTIzLDA5MjQsMDkyNSwwOTI2LDA5MjcsMDkyOCwwOTI5LDA5MzAsMDkzMSwwOTMyLDA5MzMsMDkzNCwwOTM1LDA5MzYsMDkzNywwOTM4LDA5MzksMDk0MCwwOTQxLDA5NDIsMDk0MywwOTQ0LDA5NDUsMDk0NiwwOTQ3LDA5NDgsMDk0OSwwOTUwLDA5NTEsMDk1MiwwOTUzLDA5NTQsMDk1NSwwOTU2LDA5NTcsMDk1OCwwOTU5LDA5NjAsMDk2MSwwOTYyLDA5NjMsMDk2NCwwOTY1LDA5NjYsMDk2NywwOTY4LDA5NjksMDk3MCwwOTcxLDA5NzIsMDk3MywwOTc0LDA5NzUsMDk3NiwwOTc3LDA5NzgsMDk3OSwwOTgwLDA5ODEsMDk4MiwwOTgzLDA5ODQsMDk4NSwwOTg2LDA5ODcsMDk4OCwwOTg5LDA5OTAsMDk5MSwwOTkyLDA5OTMsMDk5NCwwOTk1LDA5OTYsMDk5NywwOTk4LDA5OTksMTAwMAo='

In [29]:
data_embed = '...'

In [34]:
# HEADER
HEADER_DF = pd.read_csv(io.BytesIO(base64.b64decode(header_embed)))

# DATA
DATA_NP = ss.load_npz(io.BytesIO(base64.b64decode(data_embed))).toarray()

# COMBINE
DATA = pd.DataFrame(data=DATA_NP, columns=HEADER_DF.columns, dtype=np.uint8)

DATA

0001  0002  0003  0004  0005  0006  0007  0008  0009  0010  ...  0991  \
0        0     0     1     1     0     1     1     0     0     1  ...     0   
1        0     0     1     1     1     0     1     1     1     0  ...     0   
2        1     0     0     0     0     0     0     0     0     0  ...     0   
3        1     1     1     0     0     1     1     0     0     0  ...     1   
4        0     0     0     1     1     0     0     0     0     1  ...     0   
...    ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  ...   ...   
9995     1     0     0     0     1     1     0     1     1     1  ...     0   
9996     1     0     0     0     0     0     0     1     0     1  ...     0   
9997     0     0     0     1     1     0     1     0     0     1  ...     1   
9998     1     0     1     0     0     0     0     0     0     0  ...     0   
9999     0     0     1     0     1     0     0     1     0     1  ...     0   

      0992  0993  0994  0995  0996  0997  0998  0999  1000  
0        1     0     0     1     0     1     1     0     1  
1        1     0     0     0     1     1     0     0     1  
2        1     1     0     1     0     0     0     0     1  
3        0     1     0     1     0     0     0     1     1  
4        0     0     0     0     1     0     1     0     0  
...    ...   ...   ...   ...   ...   ...   ...   ...   ...  
9995     1     1     0     1     0     1     1     1     1  
9996     1     1     0     1     1     0     1     1     0  
9997     0     0     1     0     1     1     1     1     1  
9998     1     0     1     1     1     0     1     1     0  
9999     0     1     1     1     1     0     1     1     0  

[10000 rows x 1000 columns]

In [32]:
del DATA

#### END DEMO ************************************************************************************************